# Load data

In [1]:
import sys
sys.path.append('../')
from datasets import load_dataset
from web.model import load_model
import pandas as pd
dataset = load_dataset("taidng/UIT-ViQuAD2.0")

d:\Other\Desktop\Question_Answering\myenv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-06-05 16:14:49.891 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager


In [2]:
test_df= dataset['validation']

In [3]:
test_df = test_df.to_pandas()
test_df.head()

id      uit_id  title  \
0  0001-0001-0001  uit_000001  Paris   
1  0001-0001-0002  uit_000002  Paris   
2  0001-0001-0003  uit_000003  Paris   
3  0001-0001-0004  uit_000004  Paris   
4  0001-0001-0005  uit_000005  Paris   

                                             context  \
0  Paris nằm ở điểm gặp nhau của các hành trình t...   
1  Paris nằm ở điểm gặp nhau của các hành trình t...   
2  Paris nằm ở điểm gặp nhau của các hành trình t...   
3  Paris nằm ở điểm gặp nhau của các hành trình t...   
4  Paris nằm ở điểm gặp nhau của các hành trình t...   

                                            question  \
0  Paris đạt được thành quả gì sau khoảng 4 thế k...   
1             Vị trí địa lý của Pháp có gì đặc biệt?   
2    Kinh tế xung quanh kinh đô ánh sáng mạnh về gì?   
3                 Cuộc cách mạng Pháp diễn ra ở đâu?   
4         Kinh đô ánh sáng nổi tiếng về lĩnh vực gì?   

                                             answers  is_impossible  \
0  {'text': ['trở thành một trong những trung tâm...          False   
1                   {'text': [], 'answer_start': []}           True   
2  {'text': ['giáo dục và nghệ thuật', 'nông nghi...          False   
3         {'text': ['Paris'], 'answer_start': [358]}          False   
4  {'text': ['nghệ thuật và giải trí', 'trung tâm...          False   

                                   plausible_answers  
0                                               None  
1  {'text': ['nằm ở điểm gặp nhau của các hành tr...  
2                                               None  
3                                               None  
4                                               None

In [4]:
# Fill missing 'text' with 'plausible_answers'
def fill_missing_text(row):
    if len(row['answers']['text']) == 0:  # Check if 'text' is empty
        row['answers']['text'] = row['plausible_answers']['text']  # Fill 'text' with 'plausible_answers'
        row['answers']['answer_start'] = row['plausible_answers']['answer_start']  
    return row

test_df = test_df.apply(fill_missing_text, axis=1)

In [5]:
df = test_df[["id", "question", "answers", "context"]]

In [6]:
df['answer'] = df['answers'].apply(lambda x: x['text'])
df['answer_start'] = df['answers'].apply(lambda x: x['answer_start'])

C:\Users\LENOVO\AppData\Local\Temp\ipykernel_20532\763388355.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['answer'] = df['answers'].apply(lambda x: x['text'])
C:\Users\LENOVO\AppData\Local\Temp\ipykernel_20532\763388355.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['answer_start'] = df['answers'].apply(lambda x: x['answer_start'])


In [7]:
df= df[['id', 'question', 'context', 'answer', 'answer_start']]

In [8]:
# Convert list to string
df['answer'] = df['answer'].apply(lambda x: ', '.join(map(str, x)) if len(x) > 0 else '')
# Convert list to string
df['answer_start'] = df['answer_start'].apply(lambda x: ', '.join(map(str, x)) if len(x) > 0 else '')

In [9]:
df.head()

id                                           question  \
0  0001-0001-0001  Paris đạt được thành quả gì sau khoảng 4 thế k...   
1  0001-0001-0002             Vị trí địa lý của Pháp có gì đặc biệt?   
2  0001-0001-0003    Kinh tế xung quanh kinh đô ánh sáng mạnh về gì?   
3  0001-0001-0004                 Cuộc cách mạng Pháp diễn ra ở đâu?   
4  0001-0001-0005         Kinh đô ánh sáng nổi tiếng về lĩnh vực gì?   

                                             context  \
0  Paris nằm ở điểm gặp nhau của các hành trình t...   
1  Paris nằm ở điểm gặp nhau của các hành trình t...   
2  Paris nằm ở điểm gặp nhau của các hành trình t...   
3  Paris nằm ở điểm gặp nhau của các hành trình t...   
4  Paris nằm ở điểm gặp nhau của các hành trình t...   

                                              answer answer_start  
0  trở thành một trong những trung tâm văn hóa củ...          565  
1  nằm ở điểm gặp nhau của các hành trình thương ...            6  
2                giáo dục và nghệ thuật, nông nghiệp     323, 109  
3                                              Paris          358  
4  nghệ thuật và giải trí, trung tâm văn hóa của ...     634, 591

In [10]:
answer_actual = df['answer']
answer_actual.head()

0    trở thành một trong những trung tâm văn hóa củ...
1    nằm ở điểm gặp nhau của các hành trình thương ...
2                  giáo dục và nghệ thuật, nông nghiệp
3                                                Paris
4    nghệ thuật và giải trí, trung tâm văn hóa của ...
Name: answer, dtype: object

In [11]:
# Remove duplicates in answers
# With each answer, split the parts separated by commas, then remove the duplicates that are contained in another part
def remove_duplicates(text):
    parts = [item.strip() for item in text.split(',')]
    for i in range(len(parts)):
        for j in range(i + 1, len(parts)):
            if parts[i] in parts[j]:
                return ', '.join([item for item in parts if item != parts[i]])
            elif parts[j] in parts[i]:
                return ', '.join([item for item in parts if item != parts[j]])
    return text

# Filter records based on the remove_duplicates function
answer_actual = answer_actual.apply(remove_duplicates)
answer_actual.head()

0    trở thành một trong những trung tâm văn hóa củ...
1    nằm ở điểm gặp nhau của các hành trình thương ...
2                  giáo dục và nghệ thuật, nông nghiệp
3                                                Paris
4    trung tâm văn hóa của thế giới, thủ đô của ngh...
Name: answer, dtype: object

### Evaluate Model

Để đánh giá mô hình, nhóm em sử dụng hai độ đo: *Exact Match* và *F1 score*, với cách tính như sau:
* Exact Match (EM): 
    * Đối với mỗi cặp câu hỏi và câu trả lời (*question - answer*), nếu các ký tự trong dự đoán (*prediction*) của mô hình hoàn toàn khớp với các ký tự trong câu trả lời đúng thì EM = 1, nếu không thì EM = 0. 
    * Đây là một chỉ số nghiêm ngặt; chỉ cần sai một ký tự cũng sẽ dẫn đến EM = 0. 
* F1 score: 
    * Được tính dựa trên số các từ riêng lẻ của câu trả lời đúng xuất hiện trong dự đoán. 
    * F1 = 2 * (precision * recall) / (precion + recall)
    Trong đó:
        - *precision* là tỷ lệ giữa số lượng từ chung trên tổng số từ của *prediction*.
        - *recall* là tỷ lệ giữa số lượng từ chung trên tổng số từ của *answer*.

In [12]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained('xlm-roberta-large')
model = load_model('../model/qa_large_model/')

2024-06-05 16:15:10.031 
  command:

    streamlit run d:\Other\Desktop\Question_Answering\myenv\Lib\site-packages\ipykernel_launcher.py [ARGUMENTS]
2024-06-05 16:15:10.031 No runtime found, using MemoryCacheStorageManager


In [13]:
question = list(df['question'])
context = list(df['context'])
answer_actual = list(answer_actual)

In [14]:
import string, re
from collections import Counter

def normalize_text(s):
    """Removing punctuation, and standardizing whitespace are all typical text processing steps."""
    def white_space_fix(text):
        return " ".join(text.split())

    def remove_punc(text):
        exclude = set(string.punctuation)
        return "".join(ch for ch in text if ch not in exclude)

    def lower(text):
        return text.lower()

    return white_space_fix(remove_punc(lower(s)))

def compute_exact_match(prediction, truth):
    return int(normalize_text(prediction) == normalize_text(truth))

def compute_f1(prediction, truth):
    pred_tokens = normalize_text(prediction).split()
    truth_tokens = normalize_text(truth).split()

    # Count occurrences of tokens in prediction and truth
    pred_count = Counter(pred_tokens)
    truth_count = Counter(truth_tokens)

    # Calculate common tokens
    common_tokens = set(pred_tokens) & set(truth_tokens)

    # if there are no common tokens then f1 = 0
    if len(common_tokens) == 0:
        return 0

    # Calculate precision and recall
    prec = sum([min(pred_count[token], truth_count[token]) for token in common_tokens]) / sum(pred_count.values())
    rec = sum([min(pred_count[token], truth_count[token]) for token in common_tokens]) / sum(truth_count.values())

    # Calculate F1-score
    if prec + rec == 0:
        return 0
    else:
        return 2 * (prec * rec) / (prec + rec)

In [15]:
import torch

def run_prediction(model, tokenizer, context, question, answer_actual):
    inputs = tokenizer.encode_plus(
        question, context, 
        return_tensors='pt',
        max_length=512,
        truncation=True
    ).to('cpu')
    
    with torch.no_grad():
        outputs = model(**inputs)
    
    answer_start = torch.argmax(outputs[0])  
    answer_end = torch.argmax(outputs[1]) + 1 

    predicted_answer = tokenizer.convert_tokens_to_string(
        tokenizer.convert_ids_to_tokens(
            inputs.input_ids[0][answer_start:answer_end]
        )
    )
    
    print(
        f'- Question: {question}\n'
        f'- Context: {context}\n'
        f'- Predicted answer: {predicted_answer}\n'
        f'- Actual answer: {answer_actual}'
    )

    # Calculate accuracy and F1-score
    exact_match = compute_exact_match(predicted_answer, answer_actual)
    f1 = compute_f1(predicted_answer, answer_actual)

    print(f'- Exact Match: {exact_match}\n- F1-score: {f1}')

    return question, predicted_answer, exact_match, f1

In [16]:
for question, context, answer_actual in zip(question[:], context[:], answer_actual[:]):
    run_prediction(model, tokenizer, context, question, answer_actual)
    print('---')

- Question: Paris đạt được thành quả gì sau khoảng 4 thế kỷ tính từ ngày Cách mạng Pháp diễn ra?
- Context: Paris nằm ở điểm gặp nhau của các hành trình thương mại đường bộ và đường sông, và là trung tâm của một vùng nông nghiệp giàu có. Vào thế kỷ 10, Paris đã là một trong những thành phố chính của Pháp cùng các cung điện hoàng gia, các tu viện và nhà thờ. Từ thế kỷ 12, Paris trở thành một trong những trung tâm của châu Âu về giáo dục và nghệ thuật. Thế kỷ 14, Paris là thành phố quan trọng bậc nhất của Cơ Đốc giáo và trong các thế kỷ 16, 17, đây là nơi diễn ra Cách mạng Pháp cùng nhiều sự kiện lịch sử quan trọng của Pháp và châu Âu. Đến thế kỷ 19 và 20, thành phố trở thành một trong những trung tâm văn hóa của thế giới, thủ đô của nghệ thuật và giải trí.
- Predicted answer: nông nghiệp giàu có
- Actual answer: trở thành một trong những trung tâm văn hóa của thế giới, thủ đô của nghệ thuật và giải trí
- Exact Match: 0
- F1-score: 0
---
- Question: Vị trí địa lý của Pháp có gì đặc biệt?

Thống kê các giá trị Exact Match và F1 score trên tập test:

In [17]:
import re
import statistics
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd

# Define the pattern to extract data from the text
pattern = re.compile(
    r"- Question: (.+?)\n"
    r"- Context: (.+?)\n"
    r"- Predicted answer: (.+?)\n"
    r"- Actual answer: (.+?)\n"
    r"- Exact Match: (\d+)\n"
    r"- F1-score: ([\d\.]+)"
)

# Read the file content
with open('metrics_output.txt', 'r', encoding='utf-8') as file:
    content = file.read()

# Find all matches
matches = pattern.findall(content)

# Prepare lists to store statistics
exact_matches = []
f1_scores = []

# Extract data and store in lists
for match in matches:
    question, context, predicted_answer, actual_answer, exact_match, f1_score = match
    exact_match = int(exact_match)
    f1_score = float(f1_score)
    
    exact_matches.append((exact_match, question, predicted_answer, actual_answer, context))
    f1_scores.append((f1_score, question, predicted_answer, actual_answer, context))

# Create a DataFrame for easier manipulation
data = pd.DataFrame({
    'Exact Match': [em[0] for em in exact_matches],
    'F1-score': [f1[0] for f1 in f1_scores],
    'Question': [em[1] for em in exact_matches],
    'Context': [em[4] for em in exact_matches],
    'Predicted Answer': [em[2] for em in exact_matches],
    'Actual Answer': [em[3] for em in exact_matches]
})

# Calculate statistics
exact_match_avg = data['Exact Match'].mean()
f1_score_avg = data['F1-score'].mean()
print(f'Average Exact Match: {exact_match_avg:.2f}'
      f'\nAverage F1-score: {f1_score_avg:.2f}')

# Plotting
plt.figure(figsize=(14, 7))

# Bar plot for Exact Match
plt.subplot(1, 2, 1)
sns.countplot(x='Exact Match', data=data)
plt.title('Exact Match Distribution')
plt.xlabel('Exact Match')
plt.ylabel('Count')

# Histogram for F1-score
plt.subplot(1, 2, 2)
sns.histplot(data['F1-score'], bins=10, kde=True)
plt.title('F1-score Distribution')
plt.xlabel('F1-score')
plt.ylabel('Frequency')

plt.tight_layout()
plt.show()
d

Average Exact Match: 0.48
Average F1-score: 0.75


C:\Users\LENOVO\AppData\Local\Temp\ipykernel_20532\181524122.py:71: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()


NameError: name 'd' is not defined

Nhận xét:
* Dễ thấy vì tính "nghiêm ngặt" của EM, các dự đoán có EM = 1 cũng có F1-score = 1. Với các dự đoán có EM = 0, F1-score có thể dao động từ 0 đến 1.
* Từ barplot của EM, có thể thấy mô hình dự đoán khớp hoàn toàn với dữ liệu trên khoảng gần 1/2 tập test.
* Từ histogram của F1-score, có thể thấy mô hình dự đoán tương đối tốt. 

In [ ]:
# Print answers with the highest and lowest scores for each type
def print_answers(df, score_type, num_answers=None, ascending=True):
    if ascending:
        order = "thấp"
    else:
        order = "cao"

    sorted_df = df.sort_values(by=score_type, ascending=ascending).reset_index(drop=True)
   
    if num_answers is None:
        num_answers = len(sorted_df)
   
    for i in range(num_answers):
        row = sorted_df.iloc[i]
        print(f"Question: {row['Question']}")
        print(f"Context: {row['Context']}")
        print(f"Predicted Answer: {row['Predicted Answer']}")
        print(f"Actual Answer: {row['Actual Answer']}")
        print(f"{score_type}: {row[score_type]}\n")

Quan sát các dự đoán có EM = 0:

In [ ]:
# Lọc DataFrame để chỉ chứa các câu trả lời với Exact Match = 0
exact_match_0 = data[data['Exact Match'] == 0]

# In ra các câu trả lời với Exact Match = 0
print_answers(exact_match_0, 'Exact Match')

Question: Paris đạt được thành quả gì sau khoảng 4 thế kỷ tính từ ngày Cách mạng Pháp diễn ra?
Context: Paris nằm ở điểm gặp nhau của các hành trình thương mại đường bộ và đường sông, và là trung tâm của một vùng nông nghiệp giàu có. Vào thế kỷ 10, Paris đã là một trong những thành phố chính của Pháp cùng các cung điện hoàng gia, các tu viện và nhà thờ. Từ thế kỷ 12, Paris trở thành một trong những trung tâm của châu Âu về giáo dục và nghệ thuật. Thế kỷ 14, Paris là thành phố quan trọng bậc nhất của Cơ Đốc giáo và trong các thế kỷ 16, 17, đây là nơi diễn ra Cách mạng Pháp cùng nhiều sự kiện lịch sử quan trọng của Pháp và châu Âu. Đến thế kỷ 19 và 20, thành phố trở thành một trong những trung tâm văn hóa của thế giới, thủ đô của nghệ thuật và giải trí.
Predicted Answer: thành phố trở thành một trong những trung tâm văn hóa của thế giới, thủ đô của nghệ thuật và giải trí
Actual Answer: trở thành một trong những trung tâm văn hóa của thế giới, thủ đô của nghệ thuật và giải trí
Exact Match

* Có thể thấy rõ ràng hơn tính "nghiêm ngặt" của EM khi có nhiều trường hợp dự đoán đưa ra bởi mô hình là đúng một phần so với đáp án. 
* So với EM, F1 score là một độ đo phù hợp hơn và mang lại nhiều thông tin hơn trong trường hợp này.

Quan sát các dự đoán có F1-score thấp:

In [ ]:
num = 20
print(f"{num} câu trả lời có F1 score thấp nhất:")
print('---')
print_answers(data, 'F1-score', num_answers=num, ascending=True)

20 câu trả lời có F1 score thấp nhất:
---
Question: Gruzia có mục tiêu trở thành quốc gia như thế nào?
Context: Nhóm này được lãnh đạo bởi cựu bộ trưởng quốc phòng và khi ấy đang giữ chức thủ tướng chính phủ ly khai Dmitri Sanakoev đã tổ chức cái gọi là cuộc bầu cử thay thế, ngày 12 tháng 11 năm 2006 song song với cuộc bầu cử do chính quyền ly khai tại Tskhinvali tổ chức. Hội đồng bầu cử cũng đã đưa ra một kết quả rất cao, với ước tính hơn 42.000 cử tri cả người Ossetia (quận Java và Tskhinvali) và người Gruzia (Eredvi, Tamarasheni, vân vân) trong các cộng đồng Nam Ossetia và Sanakoev được thông báo đã nhận được 96% phiếu bầu. Một cuộc trưng cầu dân ý khác cũng đã được tổ chức ngay sau khi một yêu cầu khởi động các cuộc đàm phán với Gruzia về một thỏa thuận liên bang cho Nam Ossetia nhận được 94% phiếu ủng hộ. Tuy nhiên Liên minh Bảo vệ Nam Ossetia đã bác bỏ một yêu cầu từ một tổ chức phi chính phủ của Gruzia, "Gruzia Đa quốc gia", để giám sát cuộc trưng cầu này và những kết quả được đ

* Các câu trả lời trên cho thấy mô hình có nhiều khó khăn trong việc trích xuất chính xác thông tin từ ngữ cảnh phức tạp và có thể bị nhầm lẫn giữa các thông tin tương tự. 

# References

https://qa.fastforwardlabs.com/no%20answer/null%20threshold/bert/distilbert/exact%20match/f1/robust%20predictions/2020/06/09/Evaluating_BERT_on_SQuAD.html#F1